In [1]:
import numpy as np
import pandas as pd
import mlflow
import warnings
import pickle
import sys, os
import matplotlib.pyplot as plt
from matplotlib.gridspec import GridSpec
from matplotlib import ticker
from statsmodels.tsa.stattools import adfuller, acf, pacf
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.ensemble import RandomForestRegressor
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM


In [2]:
# sns.set()
%matplotlib inline
warnings.filterwarnings("ignore")

In [3]:
sys.path.append(os.path.abspath(os.path.join('../scripts')))
from file_handler import FileHandler

# Preprocessing

In [4]:
file_handler = FileHandler()
# reading the csv file
credit_df = file_handler.read_csv("../data/creditcard.csv")


In [5]:
data = credit_df.groupby("Time").agg({"Class": "mean"})
data

Class
Time           
0.0         0.0
1.0         0.0
2.0         0.0
4.0         0.0
7.0         0.0
...         ...
172785.0    0.0
172786.0    0.0
172787.0    0.0
172788.0    0.0
172792.0    0.0

[124592 rows x 1 columns]

In [6]:
scaler=MinMaxScaler(feature_range=(0,1))
data=scaler.fit_transform(np.array(data).reshape(-1,1))

In [7]:
data

array([[0.],
       [0.],
       [0.],
       ...,
       [0.],
       [0.],
       [0.]])

In [8]:
##splitting dataset into train and test split
training_size=int(len(data)*0.65)
test_size=len(data)-training_size
train_data,test_data=data[0:training_size,:],data[training_size:len(data),:1]

In [9]:
training_size,test_size

(80984, 43608)

In [10]:
# convert an array of values into a dataset matrix
def create_dataset(dataset, time_step=1):
	dataX, dataY = [], []
	for i in range(len(dataset)-time_step-1):
		a = dataset[i:(i+time_step), 0]   ###i=0, 0,1,2,3-----99   100 
		dataX.append(a)
		dataY.append(dataset[i + time_step, 0])
	return numpy.array(dataX), numpy.array(dataY)

In [11]:
import numpy
# reshape into X=t,t+1,t+2,t+3 and Y=t+4
time_step = 100
X_train, y_train = create_dataset(train_data, time_step)
X_test, ytest = create_dataset(test_data, time_step)

In [12]:
print(X_train.shape), print(y_train.shape)

(80883, 100)
(80883,)


(None, None)

In [13]:
print(X_test.shape), print(ytest.shape)

(43507, 100)
(43507,)


(None, None)

In [14]:
# reshape input to be [samples, time steps, features] which is required for LSTM
X_train =X_train.reshape(X_train.shape[0],X_train.shape[1] , 1)
X_test = X_test.reshape(X_test.shape[0],X_test.shape[1] , 1)

In [15]:
### Create the Stacked LSTM model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM

In [16]:
model=Sequential()
model.add(LSTM(50,return_sequences=True,input_shape=(100,1)))
model.add(LSTM(50,return_sequences=True))
model.add(LSTM(50))
model.add(Dense(1))
model.compile(loss='mean_squared_error',optimizer='adam')

In [17]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm (LSTM)                     │ (None, 100, 50)        │        10,400 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_1 (LSTM)                   │ (None, 100, 50)        │        20,200 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_2 (LSTM)                   │ (None, 50)             │        20,200 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 1)              │            51 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 50,851 (198.64 KB)

 Trainable params: 50,851 (198.64 KB)

 Non-trainable params: 0 (0.00 B)

In [18]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm (LSTM)                     │ (None, 100, 50)        │        10,400 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_1 (LSTM)                   │ (None, 100, 50)        │        20,200 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_2 (LSTM)                   │ (None, 50)             │        20,200 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 1)              │            51 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 50,851 (198.64 KB)

 Trainable params: 50,851 (198.64 KB)

 Non-trainable params: 0 (0.00 B)

In [19]:
model.fit(X_train,y_train,validation_data=(X_test,ytest),epochs=100,batch_size=64,verbose=1)

Epoch 1/100


 333/1264 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 78ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:25 79ms/step - loss: 0.00 ━━━━━━━━━━

 500/1264 ━━━━━━━━━━━━━━━━━━━━ 1:15 81ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 81ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 81ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 82ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 83ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 83ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 83ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:15 83ms/step - loss: 0.00 ━━━━━━━━━━

 667/1264 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:05 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 1:04 86ms/step - loss: 0.00 ━━━━━━━━━━

 834/1264 ━━━━━━━━━━━━━━━━━━━━ 52s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 52s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 52s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 52s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 52s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 51s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 50s 88ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 50s 88ms/step - loss: 0.001 ━━━━━━━━━━

...

 642/1264━━━━ 1:28 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:28 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:28 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:28 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:27 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:26 113ms/step -

 806/1264 ━━━━━━━━━━━━━━━━━━━━ 1:09 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:09 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:09 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:09 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:09 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:09 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:08 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:07 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:07 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:07 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 1:07 112ms/step - loss: 0.001 ━━━━━━━━━━━━━━━━━━━━ 

 973/1264/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 51s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 50s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 49s 112ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 48s 112ms/step - los

1140/1264 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 32s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 31s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 30s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 30s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 30s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 30s 113ms/step - loss: 0.00 ━━━━━━━━━━

1264/1264 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 13s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 12s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 11s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 11s 113ms/step - loss: 0.00 ━━━━━━━━━━━━━━━━━━━━ 11s 113ms/step - loss: 0.00 ━━━━━━━━━━